In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
from scipy import stats

# Plotting style
plt.style.use('default')
sns.set_palette("husl")

# Drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/ModelX/Dementia Prediction Dataset.csv')

/tmp/ipython-input-1330818034.py:1: DtypeWarning: Columns (20,22,24,26,28,41,44,46,48,51,61,63,65,67,69,71,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,134,156,165,176,179,189,217,220,222,224,226,228,230,232,234,236,238,240,242,244,246,248,250,252,254,256,258,260,262,264,266,268,270,272,382,397,399,401,419,421,423,432,445,454,494,574,605,613,638,674,690,704,707,710,715,727,738,744,746,803,804,809,810,811,812,820,831,833,835,837,843,904,959,960,961,969,970,971,972,982,1004,1007,1010) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/ModelX/Dementia Prediction Dataset.csv')


In [ ]:
demographic_features = [
    'NACCID', 'NACCADC', 'SEX', 'NACCAGE', 'NACCAGEB',
    'HISPANIC', 'HISPOR', 'HISPORX', 'RACE', 'RACEX',
    'RACESEC', 'RACESECX', 'RACETER', 'RACETERX', 'NACCNIHR',
    'PRIMLANG', 'PRIMLANX', 'EDUC', 'MARISTAT', 'NACCLIVS',
    'INDEPEND', 'RESIDENC', 'HANDED'
]

administrative_features = [
    'PACKET', 'FORMVER', 'VISITMO', 'VISITDAY', 'VISITYR',
    'NACCVNUM', 'NACCAVST', 'NACCNVST', 'NACCDAYS', 'NACCFDYS',
    'NACCACTV', 'NACCNOVS', 'NACCDSMO', 'NACCDSDY', 'NACCDSYR',
    'NACCNURP', 'NACCNRMO', 'NACCNRDY', 'NACCNRYR', 'NACCPAFF',
    'TELCOV', 'TELMOD', 'MODCOMM'
]

coparticipant_features = [
    'INBIRMO', 'INBIRYR', 'INSEX', 'NEWINF', 'INHISP', 'INHISPOR',
    'INHISPOX', 'INRACE', 'INRACEX', 'INRASEC', 'INRASECX',
    'INRATER', 'INRATERX', 'INEDUC', 'INRELTO', 'INRELTOX',
    'INKNOWN', 'INLIWYTH', 'INVISITS', 'INCALLS', 'INRELY', 'NACCNINR'
]

family_history_features = [
    'NACCFAM', 'NACCMOM', 'NACCDAD'
]

language_features = [
    'NACCSPNL', 'NACCENGL', 'APREFLAN', 'AYRSPAN', 'AYRENGL',
    'APCSPAN', 'APCENGL', 'ASPKSPAN', 'AREASPAN', 'AWRISPAN',
    'AUNDSPAN', 'ASPKENGL', 'AREAENGL', 'AWRIENGL', 'AUNDENGL'
]

data_availability_features = [
    'NACCFTD', 'NACCLBDM', 'NACCNMRI', 'NACCMRSA', 'NACCNAPA',
    'NACCAPSA', 'NACCACSF', 'NACCPCSF', 'NACCTCSF', 'NACCAUTP'
]

primary_targets = [
    'NACCUDSD',          # Cognitive status at UDS visit
    'DEMENTED',          # Met criteria for dementia
    'NORMCOG',           # Normal cognition and behavior
    'NACCTMCI',          # Mild cognitive impairment type
    'IMPNOMCI'           # Cognitively impaired, not MCI
]

diagnosis_targets = [
    'NACCALZD',          # Alzheimer's disease
    'NACCLBDE',          # Lewy body disease
    'NACCBVFT',          # Behavioral variant FTD
    'NACCPPA',           # Primary progressive aphasia
    'CVD',               # Vascular brain injury
    'PARK',              # Parkinson's disease
    'PSP',               # Progressive supranuclear palsy
    'CORT',              # Corticobasal degeneration
    'DEP',               # Depression
    'ALCDEM'             # Cognitive impairment due to alcohol
]

syndrome_targets = [
    'AMNDEM',            # Amnestic multidomain dementia
    'PCA',               # Posterior cortical atrophy
    'NACCPPAG',          # PPA subtype (Gorno-Tempini)
    'NACCLBDS',          # Lewy body dementia syndrome
    'NAMNDEM'            # Non-amnestic multidomain dementia
]

# All non-medical features combined
all_non_medical_features = (demographic_features + administrative_features +
                           coparticipant_features + family_history_features +
                           language_features + data_availability_features)

# Main targets for classification
main_targets = primary_targets + ['NACCALZD']  # Add Alzheimer's as key target

# All non-medical features combined
all_non_medical_features = (demographic_features + administrative_features +
                           coparticipant_features + family_history_features +
                           language_features + data_availability_features)

# Main targets for classification
main_targets = primary_targets + ['NACCALZD']  # Add Alzheimer's as key target

In [ ]:
def plot_non_medical_scatter(df, x_col, y_col, color_col, size_col=None, title=None):
    """ Function to make scatter plots"""

    # Check if columns exist
    missing_cols = [col for col in [x_col, y_col, color_col, size_col]
                   if col is not None and col not in df.columns]
    if missing_cols:
        print(f"❌ Missing columns: {missing_cols}")
        return

    # Filter out medical features (double-check)
    non_medical_safe = all(col in demographic_features + administrative_features +
                          coparticipant_features + family_history_features +
                          language_features for col in [x_col, y_col]
                          if col is not None)

    cols = [c for c in [x_col, y_col, color_col, size_col] if c is not None]
    plot_data = df[cols].copy().dropna()

    if title is None:
        title = f"NON-MEDICAL: {y_col} vs {x_col}"
        if color_col:
            title += f" by {color_col}"

    fig = px.scatter(
        plot_data,
        x=x_col,
        y=y_col,
        color=color_col,
        size=size_col,
        title=title,
        height=500,
        opacity=0.7,
        hover_data=plot_data.columns.tolist()
    )

    # Add trendline for numerical vs numerical
    if (plot_data[x_col].dtype in ['int64', 'float64'] and
        plot_data[y_col].dtype in ['int64', 'float64']):
        fig.update_traces(
            marker=dict(size=8, line=dict(width=1, color='DarkSlateGrey'))
        )

    fig.show()

    # Print correlation if both numerical
    if (plot_data[x_col].dtype in ['int64', 'float64'] and
        plot_data[y_col].dtype in ['int64', 'float64']):
        correlation = plot_data[x_col].corr(plot_data[y_col])
        print(f"📊 Correlation between {x_col} and {y_col}: {correlation:.3f}")

# Basic demographic scatter plots
plot_non_medical_scatter(df, 'NACCAGE', 'EDUC', color_col='SEX',
                        title='NON-MEDICAL: Education vs Age by Gender')

📊 Correlation between NACCAGE and EDUC: -0.043


In [ ]:
def plot_age_relationships(df):
    """Plot various age relationships with NON-MEDICAL features"""

    print("👥 AGE RELATIONSHIPS WITH NON-MEDICAL FEATURES")
    print("=" * 50)

    # Age vs Education by various demographics
    plot_non_medical_scatter(df, 'NACCAGE', 'EDUC', color_col='SEX',
                           title='NON-MEDICAL: Education Level vs Age by Gender')

    plot_non_medical_scatter(df, 'NACCAGE', 'EDUC', color_col='MARISTAT',
                           title='NON-MEDICAL: Education Level vs Age by Marital Status')

    # Age vs Living Situation
    if 'NACCLIVS' in df.columns:
        plot_non_medical_scatter(df, 'NACCAGE', 'NACCLIVS', color_col='SEX',
                               title='NON-MEDICAL: Living Situation vs Age by Gender')

    # Age vs Time in study
    if 'NACCDAYS' in df.columns:
        plot_non_medical_scatter(df, 'NACCAGE', 'NACCDAYS', color_col='SEX',
                               title='NON-MEDICAL: Days in Study vs Age by Gender')

# Run age relationships
plot_age_relationships(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def plot_education_relationships(df):
    """Plot education relationships with other NON-MEDICAL features"""

    print("🎓 EDUCATION RELATIONSHIPS WITH NON-MEDICAL FEATURES")
    print("=" * 50)

    # Education vs Various demographics
    if 'NACCLIVS' in df.columns:
        plot_non_medical_scatter(df, 'EDUC', 'NACCLIVS', color_col='SEX',
                               title='NON-MEDICAL: Living Situation vs Education by Gender')

    if 'INDEPEND' in df.columns:
        plot_non_medical_scatter(df, 'EDUC', 'INDEPEND', color_col='SEX',
                               title='NON-MEDICAL: Independence Level vs Education by Gender')

    if 'RESIDENC' in df.columns:
        plot_non_medical_scatter(df, 'EDUC', 'RESIDENC', color_col='SEX',
                               title='NON-MEDICAL: Residence Type vs Education by Gender')

    # Education vs Co-participant education
    if 'INEDUC' in df.columns:
        plot_non_medical_scatter(df, 'EDUC', 'INEDUC', color_col='SEX',
                               title='NON-MEDICAL: Subject vs Co-participant Education by Gender')

# Run education relationships
plot_education_relationships(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def plot_time_relationships(df):
    """Plot time and visit relationships with NON-MEDICAL features"""

    print("🕒 TIME & VISIT RELATIONSHIPS WITH NON-MEDICAL FEATURES")
    print("=" * 50)

    # Days in study vs various features
    if 'NACCDAYS' in df.columns:
        plot_non_medical_scatter(df, 'NACCDAYS', 'NACCAGE', color_col='SEX',
                               title='NON-MEDICAL: Age vs Days in Study by Gender')

        plot_non_medical_scatter(df, 'NACCDAYS', 'EDUC', color_col='SEX',
                               title='NON-MEDICAL: Education vs Days in Study by Gender')

        if 'NACCLIVS' in df.columns:
            plot_non_medical_scatter(df, 'NACCDAYS', 'NACCLIVS', color_col='SEX',
                                   title='NON-MEDICAL: Living Situation vs Days in Study by Gender')

    # Visit number relationships
    if 'NACCVNUM' in df.columns:
        plot_non_medical_scatter(df, 'NACCVNUM', 'NACCAGE', color_col='SEX',
                               title='NON-MEDICAL: Age vs Visit Number by Gender')

        plot_non_medical_scatter(df, 'NACCVNUM', 'EDUC', color_col='SEX',
                               title='NON-MEDICAL: Education vs Visit Number by Gender')

# Run time relationships
plot_time_relationships(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def plot_family_history_relationships(df):
    """Plot family history relationships with NON-MEDICAL features"""

    print("👨‍👩‍👧‍👦 FAMILY HISTORY RELATIONSHIPS WITH NON-MEDICAL FEATURES")
    print("=" * 50)

    family_features = ['NACCFAM', 'NACCMOM', 'NACCDAD']
    available_family = [f for f in family_features if f in df.columns]

    for family_feat in available_family:
        plot_non_medical_scatter(df, 'NACCAGE', family_feat, color_col='SEX',
                               title=f'NON-MEDICAL: {family_feat} vs Age by Gender')

        plot_non_medical_scatter(df, 'EDUC', family_feat, color_col='SEX',
                               title=f'NON-MEDICAL: {family_feat} vs Education by Gender')

# Run family history relationships
plot_family_history_relationships(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def quick_non_medical_scatters(df):
    """Quick overview of key NON-MEDICAL scatter relationships"""

    print("🎯 QUICK NON-MEDICAL SCATTER PLOT SUMMARY")
    print("=" * 50)

    # Most important relationships
    key_relationships = [
        ('NACCAGE', 'EDUC', 'SEX', 'Age vs Education by Gender'),
        ('NACCDAYS', 'NACCAGE', 'SEX', 'Age vs Time in Study by Gender'),
        ('EDUC', 'INEDUC', 'SEX', 'Subject vs Co-participant Education by Gender'),
        ('NACCAGE', 'NACCLIVS', 'SEX', 'Age vs Living Situation by Gender'),
        ('NACCVNUM', 'EDUC', 'SEX', 'Education vs Visit Number by Gender'),
    ]

    for x_col, y_col, color_col, description in key_relationships:
        if all(col in df.columns for col in [x_col, y_col, color_col]):
            print(f"\n📊 {description}")
            plot_non_medical_scatter(df, x_col, y_col, color_col, title=description)

# Run quick summary
quick_non_medical_scatters(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def plot_demographic_distributions(df):
    """Plot key demographic distributions"""

    print("👥 DEMOGRAPHIC DISTRIBUTIONS")
    print("=" * 50)

    # Age distribution
    if 'NACCAGE' in df.columns:
        fig = px.histogram(df, x='NACCAGE', nbins=30,
                          title='Age Distribution of Subjects',
                          labels={'NACCAGE': 'Age', 'count': 'Number of Subjects'})
        fig.show()

    # Gender distribution
    if 'SEX' in df.columns:
        gender_counts = df['SEX'].value_counts()
        fig = px.pie(values=gender_counts.values, names=gender_counts.index,
                    title='Gender Distribution')
        fig.show()

    # Education distribution
    if 'EDUC' in df.columns:
        fig = px.histogram(df, x='EDUC', nbins=20,
                          title='Education Distribution (Years)',
                          labels={'EDUC': 'Years of Education'})
        fig.show()

    # Race/ethnicity distribution
    if 'NACCNIHR' in df.columns:
        race_counts = df['NACCNIHR'].value_counts().head(10)
        fig = px.bar(x=race_counts.index, y=race_counts.values,
                    title='Top 10 Race/Ethnicity Categories',
                    labels={'x': 'Race/Ethnicity', 'y': 'Count'})
        fig.show()

plot_demographic_distributions(df)

👥 DEMOGRAPHIC DISTRIBUTIONS


In [ ]:
def plot_temporal_analysis(df):
    """Plot temporal patterns in the data"""

    print("🕒 TEMPORAL ANALYSIS")
    print("=" * 50)

    # Visit frequency over time
    if 'VISITYR' in df.columns:
        visits_by_year = df['VISITYR'].value_counts().sort_index()
        fig = px.line(x=visits_by_year.index, y=visits_by_year.values,
                     title='Number of Visits Per Year',
                     labels={'x': 'Year', 'y': 'Number of Visits'})
        fig.show()

    # Age distribution over time
    if all(col in df.columns for col in ['VISITYR', 'NACCAGE']):
        age_by_year = df.groupby('VISITYR')['NACCAGE'].mean()
        fig = px.line(x=age_by_year.index, y=age_by_year.values,
                     title='Average Age of Subjects Over Time',
                     labels={'x': 'Year', 'y': 'Average Age'})
        fig.show()

    # Study duration analysis
    if 'study_duration_years' in df.columns:
        fig = px.histogram(df, x='study_duration_years', nbins=20,
                          title='Distribution of Study Duration',
                          labels={'study_duration_years': 'Years in Study'})
        fig.show()

plot_temporal_analysis(df)

🕒 TEMPORAL ANALYSIS


In [ ]:
def plot_relationship_analysis(df):
    """Plot relationships between key demographic variables"""

    print("📈 RELATIONSHIP ANALYSIS")
    print("=" * 50)

    # Age vs Education by Gender
    if all(col in df.columns for col in ['NACCAGE', 'EDUC', 'SEX']):
        fig = px.scatter(df, x='NACCAGE', y='EDUC', color='SEX',
                        title='Education vs Age by Gender',
                        opacity=0.6, trendline='lowess')
        fig.show()

    # Age vs Study Duration
    if all(col in df.columns for col in ['NACCAGE', 'study_duration_years', 'SEX']):
        fig = px.scatter(df, x='NACCAGE', y='study_duration_years', color='SEX',
                        title='Study Duration vs Age by Gender',
                        opacity=0.6)
        fig.show()

    # Education vs Family History
    if all(col in df.columns for col in ['EDUC', 'family_history_score', 'SEX']):
        fig = px.scatter(df, x='EDUC', y='family_history_score', color='SEX',
                        title='Family History Score vs Education by Gender',
                        opacity=0.6)
        fig.show()

plot_relationship_analysis(df)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
def plot_categorical_relationships(df):
    """Plot relationships between categorical variables"""

    print("📊 CATEGORICAL RELATIONSHIPS")
    print("=" * 50)

    # Education level by Gender
    if all(col in df.columns for col in ['education_level', 'SEX']):
        cross_tab = pd.crosstab(df['education_level'], df['SEX'], normalize='index') * 100
        fig = px.bar(cross_tab, barmode='group',
                    title='Education Level Distribution by Gender',
                    labels={'value': 'Percentage', 'education_level': 'Education Level'})
        fig.show()

    # Living situation by Age Group
    if all(col in df.columns for col in ['age_group', 'NACCLIVS']):
        cross_tab = pd.crosstab(df['age_group'], df['NACCLIVS'], normalize='index') * 100
        fig = px.bar(cross_tab, barmode='group',
                    title='Living Situation by Age Group',
                    labels={'value': 'Percentage'})
        fig.show()

    # Marital status by Gender
    if all(col in df.columns for col in ['MARISTAT', 'SEX']):
        cross_tab = pd.crosstab(df['MARISTAT'], df['SEX'], normalize='index') * 100
        fig = px.bar(cross_tab, barmode='group',
                    title='Marital Status by Gender',
                    labels={'value': 'Percentage'})
        fig.show()

plot_categorical_relationships(df)

📊 CATEGORICAL RELATIONSHIPS


In [ ]:
def plot_geographic_analysis(df):
    """Plot geographic distribution patterns"""

    print("🌎 GEOGRAPHIC ANALYSIS")
    print("=" * 50)

    # Subject count by center (if center data available)
    if 'NACCADC' in df.columns:
        center_counts = df['NACCADC'].value_counts().head(15)
        fig = px.bar(x=center_counts.index.astype(str), y=center_counts.values,
                    title='Top 15 Research Centers by Subject Count',
                    labels={'x': 'Center ID', 'y': 'Number of Subjects'})
        fig.show()

    # Age distribution by center
    if 'NACCADC' in df.columns and 'NACCAGE' in df.columns:
        # Take top 10 centers for clarity
        top_centers = df['NACCADC'].value_counts().head(10).index
        df_top = df[df['NACCADC'].isin(top_centers)]

        fig = px.box(df_top, x='NACCADC', y='NACCAGE',
                    title='Age Distribution by Research Center (Top 10)')
        fig.show()

    # Education level by center
    if 'NACCADC' in df.columns and 'EDUC' in df.columns:
        top_centers = df['NACCADC'].value_counts().head(10).index
        df_top = df[df['NACCADC'].isin(top_centers)]

        fig = px.box(df_top, x='NACCADC', y='EDUC',
                    title='Education Distribution by Research Center (Top 10)')
        fig.show()

plot_geographic_analysis(df)

🌎 GEOGRAPHIC ANALYSIS


In [ ]:
def plot_family_history_analysis(df):
    """Plot family history patterns"""

    print("👨‍👩‍👧‍👦 FAMILY HISTORY ANALYSIS")
    print("=" * 50)

    # Family history score distribution
    if 'family_history_score' in df.columns:
        fig = px.histogram(df, x='family_history_score',
                          title='Family History Score Distribution',
                          nbins=10)
        fig.show()

    # Family history by gender
    if all(col in df.columns for col in ['family_history_score', 'SEX']):
        fig = px.box(df, x='SEX', y='family_history_score',
                    title='Family History Score by Gender')
        fig.show()

    # Family history by age group
    if all(col in df.columns for col in ['family_history_score', 'age_group']):
        fig = px.box(df, x='age_group', y='family_history_score',
                    title='Family History Score by Age Group')
        fig.show()

    # Specific family member history
    family_members = ['NACCMOM', 'NACCDAD']
    available_members = [f for f in family_members if f in df.columns]

    for member in available_members:
        member_counts = df[member].value_counts()
        fig = px.pie(values=member_counts.values, names=member_counts.index,
                    title=f'{member} Cognitive Impairment History')
        fig.show()

plot_family_history_analysis(df)

👨‍👩‍👧‍👦 FAMILY HISTORY ANALYSIS


In [ ]:
def plot_language_analysis(df):
    """Plot language and cultural patterns"""

    print("🗣️ LANGUAGE & CULTURAL ANALYSIS")
    print("=" * 50)

    # Primary language distribution
    if 'PRIMLANG' in df.columns:
        lang_counts = df['PRIMLANG'].value_counts().head(10)
        fig = px.bar(x=lang_counts.index, y=lang_counts.values,
                    title='Top 10 Primary Languages',
                    labels={'x': 'Language', 'y': 'Count'})
        fig.show()

    # Language proficiency scores
    if 'language_proficiency_score' in df.columns:
        fig = px.histogram(df, x='language_proficiency_score',
                          title='Language Proficiency Score Distribution',
                          nbins=20)
        fig.show()

    # Language by education
    if all(col in df.columns for col in ['PRIMLANG', 'EDUC']):
        # Take top 5 languages for clarity
        top_langs = df['PRIMLANG'].value_counts().head(5).index
        df_top = df[df['PRIMLANG'].isin(top_langs)]

        fig = px.box(df_top, x='PRIMLANG', y='EDUC',
                    title='Education Level by Primary Language (Top 5)')
        fig.show()

plot_language_analysis(df)

🗣️ LANGUAGE & CULTURAL ANALYSIS


In [ ]:
def plot_study_participation(df):
    """Plot study participation patterns"""

    print("📋 STUDY PARTICIPATION PATTERNS")
    print("=" * 50)

    # Number of visits distribution
    if 'NACCVNUM' in df.columns:
        visit_counts = df['NACCVNUM'].value_counts().sort_index()
        fig = px.bar(x=visit_counts.index, y=visit_counts.values,
                    title='Distribution of Number of Visits',
                    labels={'x': 'Visit Number', 'y': 'Number of Subjects'})
        fig.show()

    # Visit frequency
    if 'visits_per_year' in df.columns:
        fig = px.histogram(df, x='visits_per_year', nbins=20,
                          title='Visit Frequency Distribution (Visits per Year)',
                          labels={'visits_per_year': 'Visits per Year'})
        fig.show()

    # Study duration categories
    if 'study_duration_category' in df.columns:
        duration_counts = df['study_duration_category'].value_counts()
        fig = px.pie(values=duration_counts.values, names=duration_counts.index,
                    title='Study Duration Categories')
        fig.show()

    # Participation status
    if 'NACCACTV' in df.columns:
        status_counts = df['NACCACTV'].value_counts()
        fig = px.pie(values=status_counts.values, names=status_counts.index,
                    title='Follow-up Status Distribution')
        fig.show()

plot_study_participation(df)

📋 STUDY PARTICIPATION PATTERNS


In [ ]:
def plot_comprehensive_analysis(df):
    """Create comprehensive multi-feature visualizations"""

    print("🎯 COMPREHENSIVE MULTI-FEATURE ANALYSIS")
    print("=" * 50)

    # Age vs Education colored by Gender and sized by Family History
    if all(col in df.columns for col in ['NACCAGE', 'EDUC', 'SEX', 'family_history_score']):
        fig = px.scatter(df, x='NACCAGE', y='EDUC', color='SEX',
                        size='family_history_score', opacity=0.6,
                        title='Age vs Education by Gender (Size = Family History Score)',
                        hover_data=['study_duration_years'])
        fig.show()

    # Education distribution by Age Group and Gender
    if all(col in df.columns for col in ['education_level', 'age_group', 'SEX']):
        cross_tab = pd.crosstab([df['age_group'], df['education_level']], df['SEX'], normalize='index') * 100
        cross_tab = cross_tab.reset_index()

        fig = px.bar(cross_tab, x='age_group', y=cross_tab.columns[2:],
                    title='Education Level by Age Group and Gender',
                    barmode='group',
                    labels={'value': 'Percentage', 'age_group': 'Age Group'})
        fig.show()

    # Study patterns by demographic groups
    if all(col in df.columns for col in ['study_duration_category', 'education_level', 'SEX']):
        # Create a grouped bar chart
        grouped_data = df.groupby(['study_duration_category', 'education_level', 'SEX']).size().reset_index(name='count')

        fig = px.bar(grouped_data, x='study_duration_category', y='count',
                    color='education_level', facet_col='SEX',
                    title='Study Duration Patterns by Education Level and Gender',
                    barmode='group')
        fig.show()

plot_comprehensive_analysis(df)

🎯 COMPREHENSIVE MULTI-FEATURE ANALYSIS


In [ ]:
def plot_advanced_distributions(df):
    """Use diverse plot types to understand distributions"""

    print("📊 ADVANCED DISTRIBUTION ANALYSIS")
    print("=" * 50)

    # Age distribution with multiple plot types
    if 'NACCAGE' in df.columns:
        fig, ((ax1, ax2), (ax3, ax4)) = plt.subplots(2, 2, figsize=(15, 10))

        # Histogram with KDE
        sns.histplot(data=df, x='NACCAGE', kde=True, ax=ax1)
        ax1.set_title('Age Distribution (Histogram + KDE)')

        # Violin plot
        sns.violinplot(data=df, y='NACCAGE', ax=ax2)
        ax2.set_title('Age Distribution (Violin Plot)')

        # ECDF plot
        sns.ecdfplot(data=df, x='NACCAGE', ax=ax3)
        ax3.set_title('Age Distribution (ECDF)')

        # Box plot
        sns.boxplot(data=df, y='NACCAGE', ax=ax4)
        ax4.set_title('Age Distribution (Box Plot)')

        plt.tight_layout()
        plt.show()

    # Education distribution with multiple views
    if 'EDUC' in df.columns:
        fig, ((ax1, ax2), (ax3, ax4)) = plt.subplots(2, 2, figsize=(15, 10))

        # Count plot for education categories
        if 'education_level' in df.columns:
            sns.countplot(data=df, x='education_level', ax=ax1, order=df['education_level'].value_counts().index)
            ax1.set_title('Education Level Counts')
            ax1.tick_params(axis='x', rotation=45)

        # Stacked histogram by gender
        if 'SEX' in df.columns:
            sns.histplot(data=df, x='EDUC', hue='SEX', multiple="stack", ax=ax2)
            ax2.set_title('Education Distribution by Gender (Stacked)')

        # Density plot by gender
        sns.kdeplot(data=df, x='EDUC', hue='SEX', common_norm=False, ax=ax3)
        ax3.set_title('Education Density by Gender')

        # Rug plot
        sns.histplot(data=df, x='EDUC', kde=True, ax=ax4)
        sns.rugplot(data=df, x='EDUC', ax=ax4)
        ax4.set_title('Education Distribution with Rug Plot')

        plt.tight_layout()
        plt.show()

plot_advanced_distributions(df)

📊 ADVANCED DISTRIBUTION ANALYSIS


In [ ]:
def plot_multidimensional_relationships(df):
    """Explore complex relationships with advanced plot types"""

    print("🎯 MULTI-DIMENSIONAL RELATIONSHIPS")
    print("=" * 50)

    # Age vs Education with multiple dimensions
    if all(col in df.columns for col in ['NACCAGE', 'EDUC', 'SEX', 'family_history_score']):
        fig = px.scatter(df, x='NACCAGE', y='EDUC',
                        color='SEX', size='family_history_score',
                        facet_col='SEX', hover_data=['MARISTAT', 'NACCLIVS'],
                        title='Age vs Education by Gender (Size = Family History)',
                        trendline='lowess')
        fig.show()

    # 3D Scatter plot
    if all(col in df.columns for col in ['NACCAGE', 'EDUC', 'study_duration_years', 'SEX']):
        fig = px.scatter_3d(df, x='NACCAGE', y='EDUC', z='study_duration_years',
                           color='SEX', opacity=0.7,
                           title='3D: Age, Education, and Study Duration by Gender')
        fig.show()

    # Parallel coordinates plot
    numerical_features = ['NACCAGE', 'EDUC', 'study_duration_years', 'family_history_score']
    available_numerical = [f for f in numerical_features if f in df.columns]

    if len(available_numerical) >= 3 and 'SEX' in df.columns:
        fig = px.parallel_coordinates(df, dimensions=available_numerical,
                                     color='SEX',
                                     title='Parallel Coordinates: Multiple Features by Gender')
        fig.show()

    # Sunburst plot for hierarchical data
    if all(col in df.columns for col in ['age_group', 'education_level', 'SEX']):
        hierarchical_data = df.groupby(['age_group', 'education_level', 'SEX']).size().reset_index(name='count')
        fig = px.sunburst(hierarchical_data, path=['age_group', 'education_level', 'SEX'], values='count',
                         title='Sunburst: Age Group → Education Level → Gender')
        fig.show()

plot_multidimensional_relationships(df)

🎯 MULTI-DIMENSIONAL RELATIONSHIPS


In [ ]:
def plot_statistical_comparisons(df):
    """Statistical comparisons between groups"""

    print("📊 STATISTICAL COMPARISONS")
    print("=" * 50)

    # Statistical summary by groups
    if all(col in df.columns for col in ['SEX', 'NACCAGE', 'EDUC']):
        # Create a detailed statistical summary
        stats_by_gender = df.groupby('SEX').agg({
            'NACCAGE': ['mean', 'median', 'std', 'min', 'max'],
            'EDUC': ['mean', 'median', 'std', 'min', 'max'],
            'NACCID': 'count'
        }).round(2)

        print("Statistical Summary by Gender:")
        print(stats_by_gender)

        # Raincloud plots (combination of boxplot, distribution, and raw data)
        fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 6))

        # Age by gender
        sns.boxplot(data=df, x='SEX', y='NACCAGE', ax=ax1)
        sns.stripplot(data=df, x='SEX', y='NACCAGE', ax=ax1, alpha=0.3, color='black')
        ax1.set_title('Age Distribution by Gender (Box + Strip)')

        # Education by gender
        sns.violinplot(data=df, x='SEX', y='EDUC', ax=ax2)
        sns.swarmplot(data=df, x='SEX', y='EDUC', ax=ax2, alpha=0.5, color='black')
        ax2.set_title('Education Distribution by Gender (Violin + Swarm)')

        plt.tight_layout()
        plt.show()

    # Pairplot for multiple numerical features
    numerical_cols = ['NACCAGE', 'EDUC', 'study_duration_years', 'family_history_score']
    available_numerical = [f for f in numerical_cols if f in df.columns]

    if len(available_numerical) >= 2 and 'SEX' in df.columns:
        # Select a sample for clarity
        sample_df = df[available_numerical + ['SEX']].dropna().sample(n=min(500, len(df)), random_state=42)

        g = sns.PairGrid(sample_df, hue='SEX', diag_sharey=False)
        g.map_upper(sns.scatterplot, alpha=0.6)
        g.map_lower(sns.kdeplot, fill=True)
        g.map_diag(sns.histplot, multiple="stack")
        g.add_legend()
        g.fig.suptitle('Pairwise Relationships Colored by Gender', y=1.02)
        plt.show()

    # Statistical significance testing visualization
    if all(col in df.columns for col in ['NACCAGE', 'SEX']):
        from scipy import stats

        # T-test visualization
        male_ages = df[df['SEX'] == 1]['NACCAGE'].dropna()
        female_ages = df[df['SEX'] == 2]['NACCAGE'].dropna()

        t_stat, p_value = stats.ttest_ind(male_ages, female_ages)

        fig, ax = plt.subplots(figsize=(10, 6))
        sns.boxplot(data=df, x='SEX', y='NACCAGE', ax=ax)
        ax.set_title(f'Age by Gender\n(T-test: p-value = {p_value:.4f})')
        plt.show()

plot_statistical_comparisons(df)

📊 STATISTICAL COMPARISONS
Statistical Summary by Gender:
    NACCAGE                          EDUC                       NACCID
       mean median    std min  max   mean median   std min max   count
SEX                                                                   
1     74.39   75.0  10.23  18  110  16.55   16.0  6.62   0  99   81788
2     74.35   75.0  10.35  18  110  15.56   16.0  6.73   0  99  113408


ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.12/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipython-input-2585367308.py", line 66, in <cell line: 0>
    plot_statistical_comparisons(df)
  File "/tmp/ipython-input-2585367308.py", line 29, in plot_statistical_comparisons
    sns.swarmplot(data=df, x='SEX', y='EDUC', ax=ax2, alpha=0.5, color='black')
  File "/usr/local/lib/python3.12/dist-packages/seaborn/categorical.py", line 2250, in swarmplot
    p.plot_swarms(
  File "/usr/local/lib/python3.12/dist-packages/seaborn/categorical.py", line 588, in plot_swarms
    _draw_figure(ax.figure)
  File "/usr/local/lib/python3.12/dist-packages/seaborn/utils.py", line 61, in _draw_figure
    fig.canvas.draw()
  File "/usr/local/lib/python3.12/dist-packages/matplotlib/backends/backend_agg.py", line 382, in draw
    self.figure.draw(self.renderer)
  File "/usr/local/lib/python3.12/dist-

TypeError: object of type 'NoneType' has no len()

Exception ignored in: 'zmq.backend.cython._zmq.Frame.__del__'
Traceback (most recent call last):
  File "_zmq.py", line 160, in zmq.backend.cython._zmq._check_rc
KeyboardInterrupt: 


In [ ]:
def plot_advanced_geographic(df):
    """Advanced geographic and spatial analysis"""

    print("🌍 ADVANCED GEOGRAPHIC ANALYSIS")
    print("=" * 50)

    # If we have center-based data, create advanced spatial visualizations
    if 'NACCADC' in df.columns:
        # Center performance and characteristics
        center_metrics = df.groupby('NACCADC').agg({
            'NACCID': 'count',
            'NACCAGE': ['mean', 'std'],
            'EDUC': ['mean', 'std'],
            'study_duration_years': 'mean',
            'SEX': lambda x: (x == 2).mean()  # Percent female
        }).round(2)

        center_metrics.columns = ['subject_count', 'avg_age', 'std_age',
                                 'avg_educ', 'std_educ', 'avg_study_years', 'pct_female']
        center_metrics = center_metrics.reset_index()

        # Bubble chart for center characteristics
        fig = px.scatter(center_metrics, x='avg_age', y='avg_educ',
                        size='subject_count', color='pct_female',
                        hover_name='NACCADC', hover_data=['avg_study_years'],
                        title='Research Center Characteristics Bubble Chart',
                        size_max=40,
                        labels={'avg_age': 'Average Age',
                               'avg_educ': 'Average Education',
                               'pct_female': 'Percentage Female',
                               'subject_count': 'Subject Count'})
        fig.show()

        # Radar chart for top centers
        top_centers = center_metrics.nlargest(5, 'subject_count')
        metrics_for_radar = ['avg_age', 'avg_educ', 'avg_study_years', 'pct_female']

        fig = go.Figure()

        for _, center in top_centers.iterrows():
            fig.add_trace(go.Scatterpolar(
                r=[center[metric] for metric in metrics_for_radar],
                theta=metrics_for_radar,
                fill='toself',
                name=f"Center {center['NACCADC']}"
            ))

        fig.update_layout(
            polar=dict(radialaxis=dict(visible=True)),
            title="Top 5 Centers: Multi-dimensional Comparison"
        )
        fig.show()

plot_advanced_geographic(df)